NoteBook1 :- Book Recommendaion System  
in this MDF Model  
We have used  2 node to generate graph.image edge,and have also created array somewhere menupeletaed the data

# Creation of Model and Graph


In [130]:
from modeci_mdf.mdf import *

# Create nodes for the model
brd = Model(id="book_recommendation_graph")

# Create a graph and add the nodes to it
book_recommendation_graph = Graph(id="book_recommendation")

brd.graphs.append(book_recommendation_graph)


# parameters of Nodes 

In [ ]:
#create a node
user_node = Node(id="user", metadata={"description":"User of the recommendation system"})
book_node = Node(id="book", metadata={"description":"Book in the recommendation system"})


# Define parameters for the user node
user_node.parameters.append(Parameter(id="level", 
                       value=["ystery", "thriller"], 
                       metadata={"description":"Name of the thunder"}))

user_node.parameters.append(Parameter(id="genre_pref",
                             value=["mystery", "thriller"], 
                             metadata={"description":"Genres preferred by the user"}))

#add output to the graph
user_node.output_ports.append(OutputPort(id="output",
                                         value="level"))

book_recommendation_graph.nodes.append(user_node)

print(book_recommendation_graph.to_yaml())

book_recommendation:
    nodes:
        user:
            metadata:
                description: User of the recommendation system
            parameters:
                level:
                    metadata:
                        description: Name of the thunder
                    value:
                    - ystery
                    - thriller
                genre_pref:
                    metadata:
                        description: Genres preferred by the user
                    value:
                    - mystery
                    - thriller
            output_ports:
                output:
                    value: level



In [ ]:
book_node = Node(id="book",
                  metadata={"description":"Book in the recommendation system"})

book_recommendation_graph.nodes.append(book_node)

book_node.input_ports.append(InputPort(id="input"))

book_node.parameters.append(Parameter(id='slope',
                                      value=1.2))
book_node.parameters.append(Parameter(id="intercept",
                                      value=3))


p1=Parameter(
    id="linear_func",
    value="input * slope + intercept",
)

book_node.parameters.append(p1)

book_node.output_ports.append(OutputPort(id="output",
                                         value="linear_func"))


# Creating an Edge between the node 

In [ ]:
from modeci_mdf.utils import simple_connect

e1 = simple_connect(user_node, book_node, book_recommendation_graph)

# Print the current structure
print(book_recommendation_graph.to_yaml())


book_recommendation:
    nodes:
        user:
            metadata:
                description: User of the recommendation system
            parameters:
                level:
                    metadata:
                        description: Name of the thunder
                    value:
                    - ystery
                    - thriller
                genre_pref:
                    metadata:
                        description: Genres preferred by the user
                    value:
                    - mystery
                    - thriller
            output_ports:
                output:
                    value: level
        book:
            metadata:
                description: Book in the recommendation system
            input_ports:
                input: {}
            parameters:
                slope:
                    value: 1.2
                intercept:
                    value: 3
                linear_func:
                    value: input * slope

In [ ]:
brd.to_json_file("book_recommendation_graph.json")
brd.to_yaml_file("book_recommendation_graph.yaml")

'book_recommendation_graph.yaml'

# Generate a graph image from the model

In [127]:
brd.to_graph_image(
        engine="dot",
        output_format="png",
        view_on_render=False,
        level=3,
        filename_root="brd",
        is_horizontal=True
    )

from IPython.display import Image
Image(filename="book_recommendation_graph.png")

Converting MDF graph: book_recommendation to graphviz (level: 3, format: png)
    Node: user
    Node: book
    Edge: edge_user_book connects user to book
Written graph image to: brd.png


FileNotFoundError: [Errno 2] No such file or directory: 'book_recommendation_graph.png'

# Execute the graph & print the output values 

In [104]:
from modeci_mdf.execution_engine import EvaluableGraph

eg = EvaluableGraph(book_recommendation_graph, verbose=False)
eg.evaluate()

print('Output of user: %s'%eg.enodes["user"].evaluable_outputs["output"].curr_value)
print('Output of Book: %s'%eg.enodes["book"].evaluable_outputs["output"].curr_value)


Init graph: book_recommendation
Evaluating graph: book_recommendation, root nodes: ['user'], with array format numpy


Exception: Error! Could not evaluate expression [input * slope + intercept] with params [input=['ystery' 'thriller'] (NP (2,) <U8), 
slope=1.2, 
intercept=3, 
linear_func=0.0,], returned [input * slope + intercept] which is a <class 'str'>

#  Change a value to a Numpy array & execute the graph again


In [ ]:
import numpy as np 
#Convert the value of the parameter to a numpy array
user_node.get_parameter('level').value = np.array([[1,2],[3,4]])

eg.evaluate()

print('Output of A:\n%s'%eg.enodes["user"].evaluable_outputs["output"].curr_value)
print('Output of B:\n%s'%eg.enodes["book"].evaluable_outputs["output"].curr_value)

Evaluating graph: book_recommendation, root nodes: ['user', 'user', 'user', 'user', 'user'], with array format numpy
Output of A:
[[1 2]
 [3 4]]
Output of B:
[[4.2 5.4]
 [6.6 7.8]]


# Stateful Parameters in MDF

In [ ]:
# Create a model 
mod = Model(id="States")
mod_graph = Graph(id="state_example")
mod.graphs.append(mod_graph)

a_node = Node(id="user")
mod_graph.nodes.append(a_node)

#https://mdf.readthedocs.io/en/latest/api/Specification.html#parameter
#Add a stateless parameter - this is a parameter which will evaluate to the same value every execution of the node (for the same external inputs)
a_node.parameters.append(Parameter(id="increment", value=1.0))

#Add a stateful parameter - this is a parameter whose value is influenced by a previous value of a parameter, possibly itself
p1 = Parameter(
    id="count",
    value="count + increment",
)
a_node.parameters.append(p1)


# Add an output port
a_node.output_ports.append(OutputPort(id="output", value="count"))

# Print the current structure
print(mod_graph.to_yaml())



state_example:
    nodes:
        user:
            parameters:
                increment:
                    value: 1.0
                count:
                    value: count + increment
            output_ports:
                output:
                    value: count



Generate a graph image from the model

In [ ]:
brd.to_graph_image(
    engine="dot",
    output_format="png",
    view_on_render=False,
    level=3,
    filename_root="states"
)

from IPython.display import Image
Image(filename="book_images_staes.png")


Converting MDF graph: book_recommendation to graphviz (level: 3, format: png)
    Node: user
    Node: book
    Edge: edge_user_book connects user to book
Written graph image to: states.png


FileNotFoundError: [Errno 2] No such file or directory: 'book_images_staes.png'

Execute the graph & print the output values

In [ ]:
#Evaluating  the graph once and printing out the output value
from modeci_mdf.execution_engine import EvaluableGraph
eg=EvaluableGraph(mod_graph,verbose=False)

eg.evaluate()

print('Output of user: %s'%eg.enodes["user"].evaluable_outputs["output"].curr_value)


Init graph: state_example
Evaluating graph: state_example, root nodes: ['user'], with array format numpy
Output of user: 1


In [ ]:
dt=1
duration=5
t=0
time=[]
while t<duration :
    time.append(t)
    print("==== Evaluation at t = %s  " % (t))

    if t==0:
        eg.evaluate(array_format=format)
    else:
        eg.evaluate(time_increment=dt)

    print('Output of user :%s'%eg.enodes["user"].evaluable_outputs['output'].curr_value)


==== Evaluation at t = 0  
Evaluating graph: state_example, root nodes: ['user'], with array format <built-in function format>
Output of user :4
==== Evaluation at t = 0  
Evaluating graph: state_example, root nodes: ['user'], with array format <built-in function format>
Output of user :5
==== Evaluation at t = 0  
Evaluating graph: state_example, root nodes: ['user'], with array format <built-in function format>
Output of user :6
==== Evaluation at t = 0  
Evaluating graph: state_example, root nodes: ['user'], with array format <built-in function format>
Output of user :7
==== Evaluation at t = 0  
Evaluating graph: state_example, root nodes: ['user'], with array format <built-in function format>
Output of user :8
==== Evaluation at t = 0  
Evaluating graph: state_example, root nodes: ['user'], with array format <built-in function format>
Output of user :9
==== Evaluation at t = 0  
Evaluating graph: state_example, root nodes: ['user'], with array format <built-in function format>
Out

KeyboardInterrupt: 

Conditions in MDF

In [136]:
#import the necessary package to use Conditions in MDF
import graph_scheduler

book_recommendation_graph.id = 'book_recommendation_graph'

book_node = Node(id="book")
mod_graph.nodes.append(book_node)

# Add a parameters
book_node.parameters.append(Parameter(id="param_Book", value="param_B + 1"))

# Add an output port
book_node.output_ports.append(OutputPort(id="output", value="param_B"))

# Print current structure as YAML
print(mod_graph.to_yaml())

state_example:
    nodes:
        user:
            parameters:
                increment:
                    value: 1.0
                count:
                    value: count + increment
            output_ports:
                output:
                    value: count
        book:
            parameters:
                param_Book:
                    value: param_B + 1
            output_ports:
                output:
                    value: param_B



Add Conditions

In [137]:
#This condition means that A is always executed
cond_a = Condition(type="Always")

#This condition means that B will execute when A has run 3 times
cond_b = Condition(type="EveryNCalls", dependencies=user_node.id, n=3)  


In [138]:
#add the conditions to the Graph
book_recommendation_graph.conditions = ConditionSet(
    node_specific={user_node.id: cond_a, book_node.id: cond_b},
)

# Print the current structure
print(book_recommendation_graph.to_yaml())

book_recommendation_graph:
    conditions:
        node_specific:
            user:
                type: Always
                kwargs: {}
            book:
                type: EveryNCalls
                kwargs:
                    dependencies: user
                    n: 3



Generate Graph image from the model

In [139]:
brd.to_graph_image(
        engine="dot",
        output_format="png",
        view_on_render=False,
        level=2,
        filename_root="conditions_based"
    )

from IPython.display import Image
Image(filename="contion_based.png")

Converting MDF graph: book_recommendation_graph to graphviz (level: 2, format: png)
Written graph image to: conditions_based.png


FileNotFoundError: [Errno 2] No such file or directory: 'contion_based.png'

Execute the Graph 

In [140]:

from modeci_mdf.execution_engine import EvaluableGraph

eg = EvaluableGraph(book_recommendation_graph, verbose=False)
eg.evaluate()

#The Output of A expected to be 3 as it executes 3 times
print('Output of user: %s'%eg.enodes["user"].evaluable_outputs["output"].curr_value) 

#The Output of B expected to be 1 as it executes only once
print('Output of book: %s'%eg.enodes["book"].evaluable_outputs["output"].curr_value) 


Init graph: book_recommendation_graph
Evaluating graph: book_recommendation_graph, root nodes: [], with array format numpy


AttributeError: 'NoneType' object has no attribute 'id'